# Iteración inicial de modelos predictivos

In [1]:
import pandas as pd
import numpy as np

import missingno as msno
import matplotlib.pyplot as plt
import plotly.express as px

from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split 
from sklearn.decomposition import PCA
from sklearn.pipeline import Pipeline
from sklearn.decomposition import TruncatedSVD

from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import OneHotEncoder
import datetime
from dateutil.parser import parse
from sklearn.tree import  DecisionTreeClassifier
import plotly.graph_objects as go
import umap
from imblearn.under_sampling import RandomUnderSampler
from imblearn.over_sampling import RandomOverSampler

In [2]:
# Seteo jupyter notebook
pd.set_option('display.max_columns', None)

In [3]:
Data=pd.read_csv("consolidation_30May2022.csv").drop(columns=["Unnamed: 0"]).fillna("")
Data.head()

c:\Users\Jose Luis\anaconda3\envs\Programacion_Cientifica\lib\site-packages\IPython\core\interactiveshell.py:3441: DtypeWarning: Columns (40) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


pref_B-B  pref_D-E  pref_C-D  pref_A-A  Duracion_Campaña    B    C  \
0       0.0       0.0       0.0       0.0               1.0  4.0  5.0   
1       0.0       0.0       0.0       0.0               1.0  6.0  6.0   
2       0.0       0.0       0.0       0.0               1.0  2.0  3.0   
3       0.0       0.0       0.0       0.0               1.2  7.0  3.0   
4       0.0       0.0       0.0       0.0               1.0  4.0  1.0   

   lec_B-B  lec_E-E  lec_D-E  lec_C-D  lec_A-A  num_comunicaciones  Length  \
0      5.0      0.0      0.0      0.0      0.0                22.0     371   
1      8.0      0.0      1.0      1.0      0.0                15.0     371   
2      1.0      0.0      0.0      1.0      0.0                26.0     371   
3      5.0      0.0      0.0      2.0      2.0                34.0     371   
4      1.0      0.0      0.0      0.0      0.0                24.0     371   

           Monto  Frequency  Periodicity     Recency  F-D  F-H  F-I  F-J  G-K  \
0  180754.821871        396         91.0  652.012626   17   19    2   19   47   
1  154439.534968        416        102.0  649.634615    2   17   16   17  266   
2  128719.371341        395        107.0  629.587342    2   15   13   17  272   
3  142752.939212        698         69.0  690.118911   15    0    0   19  144   
4  127120.640500        374        112.0  613.438503    0   19    0   19  284   

   A-G  A-K  C-C  D-F  E-F  A-L  Positivo  Negativo  Sin Info        Edad  \
0   18  274    0    0    0    0        36       342        18  Mayor a 70   
1   16   69    0    2    3    0        23       377        16  Mayor a 70   
2   20   51    0    2    0    0        22       353        20  Mayor a 70   
3   20  465    0    0   15    6        54       624        20  Mayor a 70   
4   17   27    0    3    1    0        23       334        17  Mayor a 70   

   Sexo Renta  Recibe_sueldo_en_cuenta Segmento_consumidor Meses_antiguedad  \
0     1    R1                        0                   A  Mayor a 10 años   
1     1    R4                        0                   A  Mayor a 10 años   
2     1    R5                        0                   A  Mayor a 10 años   
3     1    R9                        0                   A  Mayor a 10 años   
4     0    R2                        0                   B  Mayor a 10 años   

  Comuna Ciudad Estado_civil Principalidad Profesion       Target  
0  331.0   13.0            D             B      P164               
1   91.0   13.0            D             B       P85  E-E B-B D-E  
2   34.0    5.0            B             C      P143      D-E A-A  
3  331.0   13.0            B             C        P1          E-E  
4   37.0    5.0            D             F      P210          D-E

In [4]:
# datos númericos
numerical=list(Data.select_dtypes(exclude=["category","object"]).columns)
numerical.remove("Sexo")
numerical.remove('Recibe_sueldo_en_cuenta')


# datos categorical
categorical=list(Data.select_dtypes(include=["category","object"]).columns)+['Sexo','Recibe_sueldo_en_cuenta']
categorical.remove("Target")

In [5]:
for i in categorical:
    Data[i]=Data[i].astype(str)

In [6]:
X=Data[numerical+categorical]
X.head()

pref_B-B  pref_D-E  pref_C-D  pref_A-A  Duracion_Campaña    B    C  \
0       0.0       0.0       0.0       0.0               1.0  4.0  5.0   
1       0.0       0.0       0.0       0.0               1.0  6.0  6.0   
2       0.0       0.0       0.0       0.0               1.0  2.0  3.0   
3       0.0       0.0       0.0       0.0               1.2  7.0  3.0   
4       0.0       0.0       0.0       0.0               1.0  4.0  1.0   

   lec_B-B  lec_E-E  lec_D-E  lec_C-D  lec_A-A  num_comunicaciones  Length  \
0      5.0      0.0      0.0      0.0      0.0                22.0     371   
1      8.0      0.0      1.0      1.0      0.0                15.0     371   
2      1.0      0.0      0.0      1.0      0.0                26.0     371   
3      5.0      0.0      0.0      2.0      2.0                34.0     371   
4      1.0      0.0      0.0      0.0      0.0                24.0     371   

           Monto  Frequency  Periodicity     Recency  F-D  F-H  F-I  F-J  G-K  \
0  180754.821871        396         91.0  652.012626   17   19    2   19   47   
1  154439.534968        416        102.0  649.634615    2   17   16   17  266   
2  128719.371341        395        107.0  629.587342    2   15   13   17  272   
3  142752.939212        698         69.0  690.118911   15    0    0   19  144   
4  127120.640500        374        112.0  613.438503    0   19    0   19  284   

   A-G  A-K  C-C  D-F  E-F  A-L  Positivo  Negativo  Sin Info        Edad  \
0   18  274    0    0    0    0        36       342        18  Mayor a 70   
1   16   69    0    2    3    0        23       377        16  Mayor a 70   
2   20   51    0    2    0    0        22       353        20  Mayor a 70   
3   20  465    0    0   15    6        54       624        20  Mayor a 70   
4   17   27    0    3    1    0        23       334        17  Mayor a 70   

  Renta Segmento_consumidor Meses_antiguedad Comuna Ciudad Estado_civil  \
0    R1                   A  Mayor a 10 años  331.0   13.0            D   
1    R4                   A  Mayor a 10 años   91.0   13.0            D   
2    R5                   A  Mayor a 10 años   34.0    5.0            B   
3    R9                   A  Mayor a 10 años  331.0   13.0            B   
4    R2                   B  Mayor a 10 años   37.0    5.0            D   

  Principalidad Profesion Sexo Recibe_sueldo_en_cuenta  
0             B      P164    1                       0  
1             B       P85    1                       0  
2             C      P143    1                       0  
3             C        P1    1                       0  
4             F      P210    0                       0

In [7]:
Y=Data["Target"]
Y.head()

0               
1    E-E B-B D-E
2        D-E A-A
3            E-E
4            D-E
Name: Target, dtype: object

In [8]:
# Generación de conjuntos de train y test
Xtrain, Xtest, Ytrain, Ytest = train_test_split(
    X, Y, test_size=0.33, 
    shuffle=True,
    
) 

In [9]:
# RUS (ELimina aleatorias clases mayoritaria):
rus=RandomUnderSampler(random_state=0) # Random_state=0

In [10]:
# Sobremuestreo: Aumentar numero de datos de la clase minoritaria
# ROS(Duplica clases):
ros=RandomOverSampler(random_state=0) # Random_state=0

In [11]:
# ROS:
Xtrain, Ytrain=ros.fit_resample(Xtrain,Ytrain)

In [12]:
# Visualización
px.histogram(Ytrain, x="Target",title="Distribution Plot Target")

**Todas las variables**

In [13]:
preprocessing_transformer = ColumnTransformer(
    transformers=[('OneHotEncoder', OneHotEncoder(handle_unknown="ignore"), categorical),
        ('MinMax', MinMaxScaler(),numerical),
    ])

In [14]:
pipe = Pipeline(
    [("preprocesamiento", preprocessing_transformer),
     #("Selection", SelectPercentile(f_classif, percentile=80)),
     #("red_atributos",TruncatedSVD(n_components=300)),
     ("clf",RandomForestClassifier(random_state=1))]
)


In [15]:
# Entrenamiento de pipelines
pipe.fit(Xtrain, Ytrain)


Pipeline(steps=[('preprocesamiento',
                 ColumnTransformer(transformers=[('OneHotEncoder',
                                                  OneHotEncoder(handle_unknown='ignore'),
                                                  ['Edad', 'Renta',
                                                   'Segmento_consumidor',
                                                   'Meses_antiguedad', 'Comuna',
                                                   'Ciudad', 'Estado_civil',
                                                   'Principalidad', 'Profesion',
                                                   'Sexo',
                                                   'Recibe_sueldo_en_cuenta']),
                                                 ('MinMax', MinMaxScaler(),
                                                  ['pref_B-B', 'pref_D-E',
                                                   'pref_C-D', 'pref_A-A',
                                                   'Duracion

In [16]:
# Generación de predicciones
Ypred = pipe.predict(Xtest)
# Métricas de evaluación 
print(classification_report(Ypred, Ytest))

c:\Users\Jose Luis\anaconda3\envs\Programacion_Cientifica\lib\site-packages\sklearn\metrics\_classification.py:1308: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.



              precision    recall  f1-score   support

                   0.82      0.61      0.70      5484
         A-A       0.13      0.61      0.22       110
     A-A B-B       0.01      0.50      0.02         4
     A-A D-E       0.00      0.00      0.00         0
         B-B       0.47      0.38      0.42      1934
     B-B C-D       0.07      0.42      0.13        36
     B-B D-E       0.12      0.23      0.15       527
 B-B D-E E-E       0.00      0.00      0.00        12
     B-B E-E       0.05      0.21      0.08        85
 B-B E-E D-E       0.01      0.12      0.02        17
         C-D       0.80      0.52      0.63      1534
     C-D B-B       0.37      0.43      0.40       399
 C-D B-B D-E       0.27      0.30      0.28       266
     C-D D-E       0.52      0.37      0.43       736
 C-D D-E B-B       0.18      0.21      0.20       263
     C-D E-E       0.59      0.55      0.57       445
 C-D E-E D-E       0.39      0.61      0.47       119
         D-E       0.59    

c:\Users\Jose Luis\anaconda3\envs\Programacion_Cientifica\lib\site-packages\sklearn\metrics\_classification.py:1308: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.

c:\Users\Jose Luis\anaconda3\envs\Programacion_Cientifica\lib\site-packages\sklearn\metrics\_classification.py:1308: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.



**Criterio CorrKill**

**Criterio Información Gini**

**Criterio solo Top correlación**